In [99]:
import spacy

import pycrfsuite as crfs

import json
import os
import re
from time import time
from nltk.tokenize import sent_tokenize


In [100]:
# Hacer funciron que lea las sentencias del documento de sentencias y las pase por la siguiente funcion iterativamente (solo las que tengan negación. Así que coger el fichero de negaciones y mirar si hay una en esa frase y entonce pasar)
# Hacer una funcion que convierta cada sentencia en una lista de tokens con las features correspondientes
# Pasar lo que devuelva la funcion a una lista mas grando, qie serà el training dataset
# Hacer  una función para passar las sentencias al CRF y que se entrene (basado en el scope)
# Hacer una función para que testear el funcionamiento del CRF

In [109]:
# Load the Spanish language model
nlp = spacy.load("es_core_news_sm")
nlp.disable_pipes('ner', 'parser')

# Function to read sentences from a file and store them in a dictionary
def read_file(file_path):
    sentences = []
    with open(file_path, 'r') as file:
        for line in file:
            sentences.append(line.strip())
    return sentences

# Function to process text data
def process_text(data, negations, output_file):
    final_sentences=[]
    final_sentences_chars = []
    for i in range(len(data)):
        text = data[i]['data']['text']
        chars = list(text)
        for value in data[i]['predictions'][0]['result']:
            index = (value['value']['start'], value['value']['end'])
            label = value['value']['labels'][0]
            for j in range(index[0], index[1]-1):
                if(chars[j] != " "): chars[j] = label.lower() #!SIGUE HABIENDO ERRORES. Tendré que cambiar lo de los puntos en  numeros yo creo
        original_text = ''.join(chars)
        sentences=sent_tokenize(text)
        final_sentences.extend(sentences)
        sentences_chars=sent_tokenize(original_text)
        final_sentences_chars.extend(sentences_chars)

    return final_sentences, final_sentences_chars

def get_only_negated_sentences(sentences, sentences_chars):
    print(len(sentences), len(sentences_chars))
    filtered_sentences=[]
    filtered_sentences_char=[]
    
    for sentence, char_sentence in zip(sentences, sentences_chars):
        if(sentence!=char_sentence):
            print(sentence, char_sentence)
            filtered_sentences.append(sentence)
            filtered_sentences_char.append(char_sentence)
    return filtered_sentences, filtered_sentences_char

def from_sentences_to_tokenfeatures(sentences):
    feature_sentences=[]
    # Process each sentence
    for sentence in sentences:
        feature_words=[]
        # Process the sentence with SpaCy
        doc = nlp(sentence)
        
        # Extract base forms, part-of-speech tags, chunk tags, and named entity tags
        base_forms = [token.lemma_ for token in doc]
        pos_tags = [token.pos_ for token in doc]
        chunk_tags = [token.dep_ for token in doc]
        
        # Output the results in a tab-separated format
        for token, lemma, pos, chunk in zip(doc, base_forms, pos_tags, chunk_tags):
            #print(f"{token.text}\t{lemma}\t{pos}\t{chunk}\t{ner}")
            feature_words.append([token.text, lemma, pos, chunk])
        #print()  # Separate sentences with an empty line
        feature_sentences.append(feature_words)

    return feature_sentences

def from_sentences_to_BIO_tagging(sentences, sentences_char): 

    tagged_sentences=[]
    for sentence, sentence_char in zip(sentences, sentences_char):
        doc1 = nlp(sentence)
        doc2 = nlp(sentence_char)
        sentence_list=[token.text for token in doc1]
        sentence_char_list=[token.text for token in doc2]
        #print(len(sentence_list), len(sentence_char_list))
        tagged_sentence=['O'] * len(sentence_list)
        for i, (word, word_char) in enumerate(zip(sentence_list, sentence_char_list)):
            if("NEG" in word_char):
                if(i!=0 and (tagged_sentence[i-1]=='B-NEG' or tagged_sentence[i-1]=='I-NEG')): tagged_sentence[i]='I-NEG'
                else: tagged_sentence[i]='B-NEG'
            elif("UNC" in word_char):
                if(i!=0 and (tagged_sentence[i-1]=='B-UNC' or tagged_sentence[i-1]=='I-UNC')): tagged_sentence[i]='I-UNC'
                else: tagged_sentence[i]='B-UNC'
            elif("NSCO" in word_char):
                if(i!=0 and (tagged_sentence[i-1]=='B-NSCO' or tagged_sentence[i-1]=='I-NSCO')): tagged_sentence[i]='I-NSCO'
                else: tagged_sentence[i]='B-NSCO'
            elif("USCO" in word_char):
                if(i!=0 and (tagged_sentence[i-1]=='B-USCO' or tagged_sentence[i-1]=='I-USCO')): tagged_sentence[i]='I-USCO'
                else: tagged_sentence[i]='B-USCO'
        tagged_sentences.append(tagged_sentence)
    
    return tagged_sentences

# Define feature extraction function
def token2features(tokens, i):
    token = tokens[i]
    features = {
        'token': token[0],        # The token itself
        'lemma': token[1],        # Lemma
        'pos_tag': token[2],      # POS tagging
        'chunk': token[3],        # Chunk
        'bias': 1.0
    }
    if i > 0:
        prev_token = tokens[i-1]
        features.update({
            'prev_token': prev_token[0],
            'prev_pos_tag': prev_token[2],
            'prev_chunk': prev_token[3]
        })
    else:
        features['BOS'] = True  # Beginning of sequence
    if i < len(tokens)-1:
        next_token = tokens[i+1]
        features.update({
            'next_token': next_token[0],
            'next_pos_tag': next_token[2],
            'next_chunk': next_token[3]
        })
    else:
        features['EOS'] = True  # End of sequence
    return features

#TODO Me faltaria decir cual es la negación y el scope, con el BIO tagging. También pensar en como entrenar al CRF para que sepa que solo tiene que poner el scope y lo otro como O 
#TODO Continuación: podría decir que haga el BIO tagging de toda la frase, de tal modo que tambien diria el BIO tag de las negaciones. Claro, y el modelo entonces tendria que encontrar las negaciones y el scope, todo junto
#TODO:
# Pasar lo que devuelva la funcion a una lista mas grando, qie serà el training dataset
# Hacer  una función para passar las sentencias al CRF y que se entrene (basado en el scope)
# Hacer una función para que testear el funcionamiento del CRF

# Hacer un txt para negations, otro para uncertanty, otro para scopes negation y otro para scopes uncertanty

In [102]:

negations_file = '../data/negation_cue.txt'
speculations_file = '../data/speculation_cue.txt'
negation_scopes_file='../data/negation_scope.txt'
speculation_scopes_file='../data/speculation_scope.txt'

output_file_training = "../data/output_blind_negex_training.json"
output_file_testing = "../data/output_blind_negex_testing.json"

# Load training data and process
ROOT_DIR = os.path.dirname(os.path.abspath(""))
data_training = json.load(open(os.path.join(ROOT_DIR, "data", "training_data.json")))
data_testing = json.load(open(os.path.join(ROOT_DIR, "data", "test_data.json")))

negations = read_file(negations_file)
speculations = read_file(speculations_file)
negation_scopes = read_file(negation_scopes_file)
speculation_scopes = read_file(speculation_scopes_file)


In [110]:
sentences_train, sentences_chars_train = process_text(data_training, negations, output_file_training)

filtered_sentences_train, filtered_sentences_char_train =  get_only_negated_sentences(sentences_train, sentences_chars_train)

X_training=from_sentences_to_tokenfeatures(filtered_sentences_train)
Y_training=from_sentences_to_BIO_tagging(filtered_sentences_train, filtered_sentences_char_train)

12557 12559
no habitos toxicos. negneg nsconsconsconsconsconsconsco nsconsconsconsconsconsconsco.
diverticulosis extensa insuficiencia renal cronica colelitiasis antecedentes quirurgicos: exeresis de lesiones cutaneas con anestesia local protesis total de cadera cordectomia herniorrafia inguinal proces actual varon de 81a que a raiz de episodio de hematuria macroscopica se realiza cistoscopia que es negativa para lesiones malignas pero se objetiva estenosis de uretra . diverticulosis extensa insuficiencia renal cronica colelitiasis antecedentes quirurgicos: exeresis de lesiones cutaneas con anestesia local protesis total de cadera cordectomia herniorrafia inguinal proces actual varon de 81a que a raiz de episodio de hematuria macroscopica se realiza nsconsconsconsconsconsconsconsconsconsconsco que es negnegnegnegnegnegnegneg nsconsconsconsco nsconsconsconsconsconsconsconsco nsconsconsconsconsconsconsconsco pero se objetiva estenosis de uretra .
se intentan dilataciones progresivas en e

KeyboardInterrupt: 

In [ ]:
sentences_test, sentences_chars_test = process_text(data_testing, negations, output_file_training)

filtered_sentences_test, filtered_sentences_char_test =  get_only_negated_sentences(sentences_test, sentences_chars_test)

X_testing=from_sentences_to_tokenfeatures(filtered_sentences_test)
Y_testing=from_sentences_to_BIO_tagging(filtered_sentences_test, filtered_sentences_char_test)

3278 3272
glasgow 15. sin signos de focalidad neurologica aguda. || - angiotc abdominal : port a cath con punta en ad.
glasgow 15. sin signos de focalidad neurologica aguda. - angiotc abdominal : port a cath con punta en ad.


KeyboardInterrupt: 

In [ ]:
"""sentences_train=process_text(data_training, negations, output_file_training)
print(len(sentences_train))
negated_sentences_train=get_only_negated_sentences(sentences_train, negations+speculations)
print(len(negated_sentences_train))

Y_training=from_sentences_to_BIO_tagging(negated_sentences_train, negations, "NEG", True)
Y_training=from_sentences_to_BIO_tagging(negated_sentences_train, speculations, "UNC", False, Y_training)
Y_training=from_sentences_to_BIO_tagging(negated_sentences_train, negation_scopes, "NSCO", False, Y_training)
Y_training=from_sentences_to_BIO_tagging(negated_sentences_train, speculation_scopes, "USCO", False, Y_training)"""

'sentences_train=process_text(data_training, negations, output_file_training)\nprint(len(sentences_train))\nnegated_sentences_train=get_only_negated_sentences(sentences_train, negations+speculations)\nprint(len(negated_sentences_train))\n\nY_training=from_sentences_to_BIO_tagging(negated_sentences_train, negations, "NEG", True)\nY_training=from_sentences_to_BIO_tagging(negated_sentences_train, speculations, "UNC", False, Y_training)\nY_training=from_sentences_to_BIO_tagging(negated_sentences_train, negation_scopes, "NSCO", False, Y_training)\nY_training=from_sentences_to_BIO_tagging(negated_sentences_train, speculation_scopes, "USCO", False, Y_training)'

In [ ]:
"""sentences_test=process_text(data_testing, negations, output_file_testing)
print(len(sentences_test))
negated_sentences_test=get_only_negated_sentences(sentences_test, negations+speculations)
print(len(negated_sentences_test))
X_testing=from_sentences_to_tokenfeatures(negated_sentences_test)
Y_testing=from_sentences_to_BIO_tagging(negated_sentences_test, negations, "NEG", True)
Y_testing=from_sentences_to_BIO_tagging(negated_sentences_test, speculations, "UNC", False, Y_testing)
Y_testing=from_sentences_to_BIO_tagging(negated_sentences_test, negation_scopes, "NSCO", False, Y_testing)
Y_testing=from_sentences_to_BIO_tagging(negated_sentences_test, speculation_scopes, "USCO", False, Y_testing)"""

'sentences_test=process_text(data_testing, negations, output_file_testing)\nprint(len(sentences_test))\nnegated_sentences_test=get_only_negated_sentences(sentences_test, negations+speculations)\nprint(len(negated_sentences_test))\nX_testing=from_sentences_to_tokenfeatures(negated_sentences_test)\nY_testing=from_sentences_to_BIO_tagging(negated_sentences_test, negations, "NEG", True)\nY_testing=from_sentences_to_BIO_tagging(negated_sentences_test, speculations, "UNC", False, Y_testing)\nY_testing=from_sentences_to_BIO_tagging(negated_sentences_test, negation_scopes, "NSCO", False, Y_testing)\nY_testing=from_sentences_to_BIO_tagging(negated_sentences_test, speculation_scopes, "USCO", False, Y_testing)'

In [ ]:
# Prepare data
X_train = []
y_train = []

for sentence_tokens, sentence_labels in zip(X_training, Y_training):
    X_sentence = [token2features(sentence_tokens, i) for i in range(len(sentence_tokens))]
    y_sentence = sentence_labels
    if(y_sentence): #!PARCHE PROVISIONAL AL PROBLEMA DE QUE NO VE NEGACIONES EN ALGUNA QUE OTRA FRASE Y DEVUELBE Y VACIO (EN LA FUNCION DE from_sentences_to_BIO_tagging)
        X_train.append(X_sentence)
        y_train.append(y_sentence)

# Train the CRF model
trainer = crfs.Trainer(verbose=False)
for xseq, yseq in zip(X_train, y_train):
    #print(xseq, yseq)
    trainer.append(xseq, yseq)
trainer.set_params({'c1': 1.0, 'c2': 1e-3, 'max_iterations': 50, 'feature.possible_transitions': True})
trainer.train('../data/bio_crf.crfsuite')

# Make predictions
tagger = crfs.Tagger()
tagger.open('../data/bio_crf.crfsuite')

X_test = []
y_test = []

for sentence_tokens, sentence_labels in zip(X_testing, Y_testing):
    X_sentence = [token2features(sentence_tokens, i) for i in range(len(sentence_tokens))]
    y_sentence = sentence_labels
    if(y_sentence): #!PARCHE PROVISIONAL AL PROBLEMA DE QUE NO VE NEGACIONES EN ALGUNA QUE OTRA FRASE Y DEVUELBE Y VACIO (EN LA FUNCION DE from_sentences_to_BIO_tagging)
        X_test.append(X_sentence)
        y_test.append(y_sentence)

y_pred = [tagger.tag(xseq) for xseq in X_test]





In [ ]:
y_pred_train = [tagger.tag(xseq) for xseq in X_train]

In [ ]:
for  y_t, y_p in zip(y_train, y_pred_train):
    print(y_t, y_p)


['B-NEG', 'B-NSCO', 'I-NSCO', 'O'] ['O', 'O', 'O', 'O']
['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-NSCO', 'O', 'O', 'B-NEG', 'B-NSCO', 'I-NSCO', 'I-NSCO', 'O', 'O', 'O', 'O', 'O', 'O', 'O'] ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O']
['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-NEG', 'B-NSCO', 'O'] ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O']
['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-NEG', 'B-NSCO', 'I-NSCO', 'I-NSCO', 'I-NSCO', 'O'] ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', '

In [ ]:
for sentence, y_p, y_t in zip(X_test, y_pred, y_test):
    print(len(sentence), y_p, y_t)

#TODO Hacerlo con todos los BIO taggin que hay, eso es lo que faltaria, aparte de ponerlo todo en json

142 ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'] ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O',